In [1]:
def prefill(board, h, v, n):
    def build(l, n):
        res = [0] * n
        presum, postsum = [0], [0]
        for _v in l:
            presum.append(presum[-1] + _v + 1)
        for _v in l[::-1]:
            postsum.append(postsum[-1] + _v + 1)
        postsum.pop()
        postsum = postsum[::-1]
        for i,_v in enumerate(l):
            low_e = presum[i] + (_v-1)
            high_s = n-1 - postsum[i] - (_v-1)
            for j in range(high_s, low_e+1):
                res[j] = 1
        return res
    for i in range(n):
        hm = build(h[i], n)
        vm = build(v[i], n)
        for j in range(n):
            board[i][j] = hm[j] if board[i][j] == 0 else board[i][j]
            board[j][i] = vm[j] if board[j][i] == 0 else board[j][i]
    return

In [2]:
# test if the possible line conflicts with bl
def valid(l, bl, n):
    for i in range(n):
        if bl[i] == 0:
            continue
        if l[i] != bl[i]:
            return False
    return True

# all possible lines from l in n grids
def perm(l, n):
    def dfs(l, n, idx, ls, dres):
        sls = sum(ls)
        if sls > n:
            return
        if idx == len(l):
            dres.append(ls + [n-sls])
            return
        if idx == 0:
            for g in range(n-l[idx]+1):
                dfs(l, n, idx+1, ls + [g, l[idx]], dres)
        else:
            for g in range(1, n-l[idx]+1-sls):
                dfs(l, n, idx+1, ls + [g, l[idx]], dres)
        return
    def convt(l, n):
        res = [-1] * n
        i = l[0]
        ln = len(l)
        for li in range(1, ln, 2):
            for j in range(l[li]):
                res[i+j] = 1
            i += (l[li] + l[li+1])
        return res

    dres = []
    dfs(l, n, 0, [], dres)
    res = [convt(_, n) for _ in dres]
    return res

def pos_lines(l, bl, n):
    '''
    return a list of all possible line outcomes, 
    considering restriction l and board line bl
    '''
    
#     bl represents the line on board
#     -1 -> cannot be mark
#     0 -> undetermined
#     1 -> marked
    
    return [_ for _ in perm(l, n) if valid(_, bl, n)]

def snapshot(board):
    l = [' '.join(str(_)) for _ in board]
    return '#'.join(l)

def update(ls):
    n, m = len(ls), len(ls[0])
    res = [0]*m
    for i in range(n):
        for j in range(m):
            res[j] += ls[i][j]
    for i in range(m):
        if res[i] == n:
            res[i] = 1
        elif res[i] == -n:
            res[i] = -1
        else:
            res[i] = 0
    return res

In [3]:
import copy
def vvalid(board, vpls, n):
    for i in range(n):
        if len(vpls[i]) <= 1:
            continue
        bl = [board[j][i] for j in range(n)]
        flag = False
        for pl in vpls[i]:
            if valid(pl, bl, n):
                flag = True
                break
        if not flag:
            return False
    return True
                
def dfs_fill(board, hpls, vpls, idx, n, all_outcomes):
    if idx == n:
        all_outcomes.append(copy.deepcopy(board))
        return True
    if not hpls[idx] or len(hpls[idx]) == 0:
        return dfs_fill(board, hpls, vpls, idx+1, n, all_outcomes)
    line_snap = board[idx].copy()
    for pl in hpls[idx]:
        board[idx] = pl
        vv = vvalid(board, vpls, n)
        if vv:
            dfs_fill(board,hpls, vpls, idx+1, n, all_outcomes)
#         # update the board line while checking, if fail, try next pl
#         flag1 = True
#         for i in range(n):
#             if board[idx][i] == 0:
#                 board[idx][i] = pl[i]
#                 bl = [board[j][i] for j in range(n)]
#                 # check the vline with the newly filled grid, if all vpl fail, then the update is invalid
#                 flag2 = False
#                 for vpl in vpls[i]:
#                     if valid(vpl, bl, n):
#                         flag2 = True
#                         break
#                 if not flag2:
#                     flag1 = False
#                     break
#         if flag1:
#             return dfs_fill(board, hpls, vpls, idx+1, n, all_outcomes)
    # if all pls fail, need to reset the board line for previous levels
    board[idx] = line_snap
    return False

In [4]:
def bprint(board):
    for l in board:
        print(''.join(['*' if _ == 1 else '_' for _ in l]))
    return

def lprint(ls):
    for l in ls:
        print('length of line is {}'.format(len(l)), l)
    return

In [5]:
def solve(hlist, vlist):
    hn, vn = len(hlist), len(vlist)
    if hn != vn:
        print("Line restriction input error. Lengths not equal!")
        return
    if sum([sum(_) for _ in hlist]) != sum([sum(_) for _ in vlist]):
        print("Line restriction input error. hsum and v sum not equal!")
        return
    # board nxn grid; each grid: -1 cannot mark, 0 undetermined, 1 marked
    board = [[0 for i in range(vn)] for j in range(hn)]
    prefill(board, hlist, vlist, hn)
    print("after prefill")
    bprint(board)
    print("|"*10)
    hpls , vpls = [], []
    for i in range(hn):
        hpls.append(pos_lines(hlist[i], board[i], hn))
        vpls.append(pos_lines(vlist[i], [board[j][i] for j in range(hn)], hn))
    lprint(hpls)
    print("*"*20)
    lprint(vpls)
    done = 0
    all_outcomes = []
    while True:
        snap = snapshot(board)
        change = False
        if done == hn * 2:
            print("all filled")
            print(*board, sep='\n')
            print("!!*"*10)
            return
        for i in range(hn):
            hpl = [l for l in hpls[i] if valid(l, board[i], hn)]
            if len(hpl) == 1 or len(hpl) < len(hpls[i]):
                board[i] = update(hpl)
                change = True
                if len(hpl) == 1:
                    hpls[i] = []
                    done += 1
                else:
                    hpls[i] = hpl
            vpl = [l for l in vpls[i] if valid(l, [board[j][i] for j in range(hn)], hn)]
            if len(vpl) == 1 or len(vpl) < len(vpls[i]):
                updated = update(vpl)
                change = True
                for j in range(hn):
                    board[j][i] = updated[j]
                if len(vpl) == 1:
                    vpls[i] = []
                    done += 1
                else:
                    vpls[i] = vpl
        if snap == snapshot(board) and not change:
            print("there are more than one solution")
            dfs_fill(board, hpls, vpls, 0, hn, all_outcomes)
            print('number of outcomes', len(all_outcomes))
            for i,outcome in enumerate(all_outcomes):
                print("No. {} outcome".format(i+1))
                bprint(outcome)
            break
    print("final board")
    bprint(board)
    if all_outcomes[0]:
        bprint(all_outcomes[0])
    print("*!"*10)
    return
#     print("cannot converge to one solution...")
#     print(*board, sep='\n')
#     print("to be continued......")
#     print(*hpls, sep='\n')
#     print("*"*20)
#     print(*vpls, sep='\n')
#     if fill(board, hlist, vlist, 0, hn):
#         print("all through")
#         print(*board, sep='\n')
#         print("*!"*10)
#         return
#     print("cannot get through")
#     print(":("*10)
#     print(*board, sep='\n')
# solve([[1],[2],[1,1]], [[2],[1],[1,1]])
solve([[1],[3],[1],[2]], [[1,1],[1,1],[2],[1]])

after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!


In [6]:
ls_h = '''
2
4
2 1
1 3
9
7
2 4
1 4
3 1
4 3
4 1
5
1 4
7 1 2
3
'''
ls_h = [[int(i) for i in j.split(' ')] for j in ls_h.split('\n') if j]
print(len(ls_h), ls_h)
ls_v = '''
2 1
2 1
2 1
2 1
1 3 1
8 1
3 6 1
1 8
1 8
2 3 1
2 2 1
1 2
1 1 2
3 2
1 1
'''
ls_v = [[int(i) for i in j.split(' ')] for j in ls_v.split('\n') if j]
print(len(ls_v),ls_v)

15 [[2], [4], [2, 1], [1, 3], [9], [7], [2, 4], [1, 4], [3, 1], [4, 3], [4, 1], [5], [1, 4], [7, 1, 2], [3]]
15 [[2, 1], [2, 1], [2, 1], [2, 1], [1, 3, 1], [8, 1], [3, 6, 1], [1, 8], [1, 8], [2, 3, 1], [2, 2, 1], [1, 2], [1, 1, 2], [3, 2], [1, 1]]


In [7]:
%timeit solve([[1],[2],[1,1]], [[2],[1],[1,1]])

after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!

[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all fille

**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__

length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
*******************

length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]

...

length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]

length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]

[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1

after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!

length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]]
length of line is 1 [[-1, 1, -1]]
length of line is 1 [[1, -1, 1]]
all filled
[-1, -1, 1]
[1, 1, -1]
[1, -1, 1]
!!*!!*!!*!!*!!*!!*!!*!!*!!*!!*
after prefill
__*
**_
*_*
||||||||||
length of line is 1 [[-1, -1, 1]]
length of line is 1 [[1, 1, -1]]
length of line is 1 [[1, -1, 1]]
********************
length of line is 1 [[-1, 1, 1]

In [8]:
%timeit solve([[1],[3],[1],[2]], [[1,1],[1,1],[2],[1]])

after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 

length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1

length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
*

**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]

_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -

...

**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]

__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1

final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1

length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]


length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
there are more than one solution
number of outcomes 3
No. 1 outcome
*___
_***
__*_
**__
No. 2 outcome
__*_
***_
___*
**__
No. 3 outcome
___*
***_
__*_
**__
final board
____
_**_
____
_*__
*___
_***
__*_
**__
*!*!*!*!*!*!*!*!*!*!
after prefill
____
_**_
____
____
||||||||||
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 2 [[1, 1, 1, -1], [-1, 1, 1, 1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
length of line is 3 [[1, 1, -1, -1], [-1, 1, 1, -1], [-1, -1, 1, 1]]
********************
length of line is 3 [[1, -1, 1, -1], [1, -1, -1, 1], [-1, 1, -1, 1]]
length of line is 1 [[-1, 1, -1, 1]]
length of line is 2 [[1, 1, -1, -1], [-1, 1, 1, -1]]
length of line is 4 [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1

In [9]:
%timeit solve([[1,2],[1,2],[1,2],[2],[3],[2,1],[2,1],[1,1]],[[3,2],[2],[2],[2],[6],[2],[2],[1]])

after prefill
________
________
*___*___
____*___
____*___
____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1,

________
________
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
*!*!*!*!*!*!*!*!*!*!
after prefill
________
________
*___*___
____*___
____*___
____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1,

length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 2 [[1, -

number of outcomes 1
No. 1 outcome
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
final board
________
________
*___*___
____*___
____*___
____*___
________
________
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
*!*!*!*!*!*!*!*!*!*!
after prefill
________
________
*___*___
____*___
____*___
____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -

number of outcomes 1
No. 1 outcome
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
final board
________
________
*___*___
____*___
____*___
____*___
________
________
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
*!*!*!*!*!*!*!*!*!*!
after prefill
________
________
*___*___
____*___
____*___
____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -

...

number of outcomes 1
No. 1 outcome
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
final board
________
________
*___*___
____*___
____*___
____*___
________
________
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
*!*!*!*!*!*!*!*!*!*!
after prefill
________
________
*___*___
____*___
____*___
____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -

number of outcomes 1
No. 1 outcome
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
final board
________
________
*___*___
____*___
____*___
____*___
________
________
*_____**
*____**_
*___**__
___**___
__***___
_**_*___
**__*___
*___*___
*!*!*!*!*!*!*!*!*!*!
after prefill
________
________
*___*___
____*___
____*___
____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -

length of line is 3 [[1, 1, 1, 1, 1, 1, -1, -1], [-1, 1, 1, 1, 1, 1, 1, -1], [-1, -1, 1, 1, 1, 1, 1, 1]]
length of line is 7 [[1, 1, -1, -1, -1, -1, -1, -1], [-1, 1, 1, -1, -1, -1, -1, -1], [-1, -1, 1, 1, -1, -1, -1, -1], [-1, -1, -1, 1, 1, -1, -1, -1], [-1, -1, -1, -1, 1, 1, -1, -1], [-1, -1, -1, -1, -1, 1, 1, -1], [-1, -1, -1, -1, -1, -1, 1, 1]]
length of line is 7 [[1, 1, -1, -1, -1, -1, -1, -1], [-1, 1, 1, -1, -1, -1, -1, -1], [-1, -1, 1, 1, -1, -1, -1, -1], [-1, -1, -1, 1, 1, -1, -1, -1], [-1, -1, -1, -1, 1, 1, -1, -1], [-1, -1, -1, -1, -1, 1, 1, -1], [-1, -1, -1, -1, -1, -1, 1, 1]]
length of line is 8 [[1, -1, -1, -1, -1, -1, -1, -1], [-1, 1, -1, -1, -1, -1, -1, -1], [-1, -1, 1, -1, -1, -1, -1, -1], [-1, -1, -1, 1, -1, -1, -1, -1], [-1, -1, -1, -1, 1, -1, -1, -1], [-1, -1, -1, -1, -1, 1, -1, -1], [-1, -1, -1, -1, -1, -1, 1, -1], [-1, -1, -1, -1, -1, -1, -1, 1]]
there are more than one solution
number of outcomes 1
No. 1 outcome
*_____**
*____**_
*___**__
___**___
__***___
_**_*__

____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1,

__***___
_**_*___
**__*___
*___*___
*!*!*!*!*!*!*!*!*!*!
after prefill
________
________
*___*___
____*___
____*___
____*___
________
________
||||||||||
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -1], [-1, -1, 1, -1, -1, -1, 1, 1], [-1, -1, -1, 1, -1, 1, 1, -1], [-1, -1, -1, 1, -1, -1, 1, 1], [-1, -1, -1, -1, 1, -1, 1, 1]]
length of line is 15 [[1, -1, 1, 1, -1, -1, -1, -1], [1, -1, -1, 1, 1, -1, -1, -1], [1, -1, -1, -1, 1, 1, -1, -1], [1, -1, -1, -1, -1, 1, 1, -1], [1, -1, -1, -1, -1, -1, 1, 1], [-1, 1, -1, 1, 1, -1, -1, -1], [-1, 1, -1, -1, 1, 1, -1, -1], [-1, 1, -1, -1, -1, 1, 1, -1], [-1, 1, -1, -1, -1, -1, 1, 1], [-1, -1, 1, -1, 1, 1, -1, -1], [-1, -1, 1, -1, -1, 1, 1, -

In [10]:
%timeit solve(ls_h,ls_v)

after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
||||||||||
length of line is 14 [[1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1], [-1, 1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1], [-1, -1, 1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1], [-1, -1, -1, 1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1], [-1, -1, -1, -1, 1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1], [-1, -1, -1, -1, -1, 1, 1, -1, -1, -1, -1, -1, -1, -1, -1], [-1, -1, -1, -1, -1, -1, 1, 1, -1, -1, -1, -1, -1, -1, -1], [-1, -1, -1, -1, -1, -1, -1, 1, 1, -1, -1, -1, -1, -1, -1], [-1, -1, -1, -1, -1, -1, -1, -1, 1, 1, -1, -1, -1, -1, -1], [-1, -1, -1, -1, -1, -1, -1, -1, -1, 1, 1, -1, -1, -1, -1], [-1, -1, -1, -1, -1, -1, -1, -1, -1, -1, 1, 1, -1, -1, -1], [-1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, 1, 1, -1

length of line is 20 [[1, 1, 1, 1, 1, 1, 1, -1, 1, -1, 1, 1, -1, -1, -1], [1, 1, 1, 1, 1, 1, 1, -1, 1, -1, -1, 1, 1, -1, -1], [1, 1, 1, 1, 1, 1, 1, -1, 1, -1, -1, -1, 1, 1, -1], [1, 1, 1, 1, 1, 1, 1, -1, 1, -1, -1, -1, -1, 1, 1], [1, 1, 1, 1, 1, 1, 1, -1, -1, 1, -1, 1, 1, -1, -1], [1, 1, 1, 1, 1, 1, 1, -1, -1, 1, -1, -1, 1, 1, -1], [1, 1, 1, 1, 1, 1, 1, -1, -1, 1, -1, -1, -1, 1, 1], [1, 1, 1, 1, 1, 1, 1, -1, -1, -1, 1, -1, 1, 1, -1], [1, 1, 1, 1, 1, 1, 1, -1, -1, -1, 1, -1, -1, 1, 1], [1, 1, 1, 1, 1, 1, 1, -1, -1, -1, -1, 1, -1, 1, 1], [-1, 1, 1, 1, 1, 1, 1, 1, -1, 1, -1, 1, 1, -1, -1], [-1, 1, 1, 1, 1, 1, 1, 1, -1, 1, -1, -1, 1, 1, -1], [-1, 1, 1, 1, 1, 1, 1, 1, -1, 1, -1, -1, -1, 1, 1], [-1, 1, 1, 1, 1, 1, 1, 1, -1, -1, 1, -1, 1, 1, -1], [-1, 1, 1, 1, 1, 1, 1, 1, -1, -1, 1, -1, -1, 1, 1], [-1, 1, 1, 1, 1, 1, 1, 1, -1, -1, -1, 1, -1, 1, 1], [-1, -1, 1, 1, 1, 1, 1, 1, 1, -1, 1, -1, 1, 1, -1], [-1, -1, 1, 1, 1, 1, 1, 1, 1, -1, 1, -1, -1, 1, 1], [-1, -1, 1, 1, 1, 1, 1, 1, 1, -1, -1, 1, -

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
______

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
______

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
______

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
______

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
______

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
______

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
after prefill
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
______

number of outcomes 1
No. 1 outcome
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
final board
_______________
_______________
_______________
_______________
______***______
_____*_________
_____*_________
_____****______
______***______
______***______
_______________
_______________
_______________
___****________
_______________
_____**________
____****_______
_____**_____*__
_____*___***___
__*********____
_*******_______
**__****_______
*____****______
______***____*_
______****__***
_______****__*_
_______*****___
________*__****
*******_*___**_
________***____
*!*!*!*!*!*!*!*!*!*!
2.13 s ± 86.4 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
